<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

## Data Processing Workflow

In this workflow within PyCCAPT, we can crope the data, do the voltage and bowl calibration, calculate the 3d reconstruction, and do the ranging.
</div>

In [1]:
# Activate intractive functionality of matplotlib
%matplotlib ipympl
# Activate auto reload 
%load_ext autoreload
%autoreload 2
%reload_ext autoreload
# import libraries
import os
import numpy as np
from ipywidgets import widgets
from IPython.display import display
from ipywidgets import fixed, interact_manual
import warnings
# Ignore all warnings
warnings.filterwarnings("ignore")

# Local module and scripts
from pyccapt.calibration.calibration_tools import widgets as wd
from pyccapt.calibration.data_tools import data_tools, data_loadcrop, dataset_path_qt
from pyccapt.calibration.tutorials.tutorials_helpers import helper_calibration
from pyccapt.calibration.tutorials.tutorials_helpers import helper_data_loader
from pyccapt.calibration.tutorials.tutorials_helpers import helper_temporal_crop
from pyccapt.calibration.tutorials.tutorials_helpers import helper_special_crop
from pyccapt.calibration.tutorials.tutorials_helpers import helper_t_0_tune
from pyccapt.calibration.tutorials.tutorials_helpers import helper_mc_plot
from pyccapt.calibration.tutorials.tutorials_helpers import helper_3d_reconstruction
from pyccapt.calibration.tutorials.tutorials_helpers import helper_ion_selection
from pyccapt.calibration.tutorials.tutorials_helpers import helper_visualization
from pyccapt.calibration.tutorials.tutorials_helpers import helper_ion_list

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">
In case of recieving the error about pytable library, you have to install the pytables library with conda command. to do that you can open a new cell and copy the line below in it. Then just run it like other cells. The pytables library will be innstalled.
    
`!conda install --yes --prefix {sys.prefix} pytables`
</div>


<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">
    
By clicking on the button below, you can select the dataset file you want to crop. The dataset file can be in various formats, including HDF5, EPOS, POS, ATO, and CSV. The cropped data will be saved in the same directory as the original dataset file in a new directory nammed load_crop. The name of the cropped dataset file will be the same as the original dataset file. The figures will be saved in the same directory as the dataset file.
</div>

In [2]:
button = widgets.Button(
    description='load dataset',
)
@button.on_click
def open_file_on_click(b):
    """
    Event handler for button click event.
    Prompts the user to select a dataset file and stores the selected file path in the global variable dataset_path.
    """
    global dataset_path
    dataset_path = dataset_path_qt.gui_fname().decode('ASCII')
button

Button(description='load dataset', style=ButtonStyle())

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

## ROI Selection and Data Cropping
    

</div>



<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

    
From the dropdown lists below, you can select the instrument specifications of the dataset. The instrument specifications are the same as the ones used for the calibration process. Data mode is specify the dataset structure. The dataset can be in raw or calibrated mode. The flight path length is the distance between the sample and the detector. The t0 is the time of flight of the ions with the lowest mass-to-charge ratio. The maximum mass-to-charge ratio is the maximum mass-to-charge ratio of tat you want to plot. You can also change it in te related cells. The detector diameter is the diameter of the detector.
</div>


In [22]:
# create an object for selection of instrument specifications of the dataset
tdc, pulse_mode, flight_path_length, t0, max_mc, det_diam = wd.dataset_instrument_specification_selection()

# Display lists and comboboxes to selected instrument specifications
display(tdc, pulse_mode, flight_path_length, t0, max_mc)

Dropdown(description='Data mode:', options=('pyccapt', 'leap_epos', 'leap_pos', 'ato_v6'), value='pyccapt')

Dropdown(description='Pulse mode:', options=('voltage', 'laser'), value='voltage')

FloatText(value=110.0, description='Flight path length:')

FloatText(value=38.0, description='t0:')

FloatText(value=400.0, description='Max mc:')

In [23]:
variables = helper_data_loader.load_data(dataset_path, max_mc.value, flight_path_length.value, pulse_mode.value, tdc.value)
display(variables.data)
display(variables.range_data)

The maximum possible TOF is: 5010 ns
The data will be saved on the path: C:/Users/mehrp/PycharmProjects/pyccapt/tests/data/data_115_Jul-27-2022_17-44_Powersweep3/data_processing/
The dataset name after saving is: data_115_Jul-27-2022_17-44_Powersweep3
The figures will be saved on the path: C:/Users/mehrp/PycharmProjects/pyccapt/tests/data/data_115_Jul-27-2022_17-44_Powersweep3/data_processing/
{'apt': ['high_voltage', 'num_events', 'time_counter'], 'dld': ['high_voltage', 'pulse', 'start_counter', 't', 'x', 'y'], 'tdc': ['ch0', 'ch1', 'ch2', 'ch3', 'ch4', 'ch5', 'ch6', 'ch7'], 'time': ['time_h', 'time_m', 'time_s']}
The number of data over max_tof: 30420
Total number of Ions: 892131


high_voltage (V)         pulse  start_counter  t (ns)  x_det (cm)  \
0               0.000000  1.084383e+12              0     0.0    0.000000   
1               0.000000  1.084383e+12              0     0.0    0.000000   
2               0.000000  1.084383e+12              0     0.0    0.000000   
3               0.000000  1.084383e+12              0     0.0    0.000000   
4               0.000000  1.084383e+12              0  2753.0    2.730100   
...                  ...           ...            ...     ...         ...   
892126       6900.186523  1.871629e+12              0   248.0   -2.799670   
892127       6900.186523  1.871629e+12              0  2217.0    0.807768   
892128       6900.186523  1.871629e+12              0   999.0    2.788440   
892129       6900.186523  1.871629e+12              0     7.0    1.279810   
892130       6900.186523  1.871629e+12              0  2220.0    1.371010   

        y_det (cm)  
0         0.000000  
1         0.000000  
2         0.000000  
3         0.000000  
4        -0.474107  
...            ...  
892126   -2.478320  
892127    0.780332  
892128   -0.917429  
892129   -2.385730  
892130   -2.125010  

[892131 rows x 6 columns]

ion  mass   mc  mc_low  mc_up    color   element complex isotope  \
0  unranged   0.0  0.0     0.0  400.0  #000000  unranged       0       0   

   charge  
0       0

In [25]:
#load data, if it exists,
try:
    if os.path.exists(variables.result_data_path + '//' + variables.result_data_name + '.h5'):
        variables.data = data_tools.load_data(variables.result_data_path + '//' + variables.result_data_name + '.h5', tdc='pyccapt', mode='processed')
        print('Continue from the point based on the loaded data')
    else:
        print('No data avaliable')
    if os.path.exists(variables.result_data_path + '/' + 'range_' + variables.dataset_name+ '.h5'):
        variables.range_data = data_tools.read_hdf5_through_pandas(variables.result_data_path + '/' + 'range_' + variables.dataset_name+ '.h5')
        print('Continue from the point based on the loaded data')
    else:
        print('No range data avaliable')
    # exctract needed data from Pandas data frame as a numpy array
    data_tools.extract_data(variables.data, variables, flight_path_length.value, max_mc.value)
    display(variables.data)
    display(variables.range_data)
except Exception as e:
    pass
    # print(e)

Continue from the point based on the loaded data
Continue from the point based on the loaded data
The maximum time of flight: 5010


x (nm)    y (nm)      z (nm)  mc_c (Da)     mc (Da)  \
0       2.638314 -2.708391    0.376799  92.114744   96.632159   
1      -0.452708 -1.442385    0.060484  90.535085   95.165440   
2       3.359438  1.374112    0.347794  90.998621   94.763123   
3       0.000000  0.000000    0.001620   5.961612    6.181229   
4       2.249210 -0.658095    0.145741  91.022217   95.221722   
...          ...       ...         ...        ...         ...   
514106  0.586899 -1.102312  217.152727  91.027713   95.519249   
514107 -2.261312  0.090232  217.264694   3.279549    3.385214   
514108  0.005518 -2.840600  217.358029  90.619730   95.513570   
514109  1.850265  1.477804  217.281094   3.549455    3.636425   
514110  1.749592  2.770171  217.443550  98.930123  102.882996   

        high_voltage (V)         pulse  start_counter    t_c (ns)  t (ns)  \
0            7825.044434  1.201232e+12              0   96.667549  2022.0   
1            7825.044434  1.201232e+12              0   94.964807  1990.0   
2            7825.044434  1.201232e+12              0   95.423833  2001.0   
3            7825.044434  1.201232e+12              0    6.186905   525.0   
4            7825.044434  1.201232e+12              0   95.497601  1995.0   
...                  ...           ...            ...         ...     ...   
514106       6566.107910  1.839976e+12              0   95.445040  2174.0   
514107       6566.107910  1.839976e+12              0    3.376764   431.0   
514108       6566.107910  1.839976e+12              0   94.976538  2188.0   
514109       6566.107910  1.839976e+12              0    3.656434   446.0   
514110       6566.107910  1.839976e+12              0  103.610663  2276.0   

        x_det (cm)  y_det (cm)  pulse_pi  ion_pp  
0         2.461500   -2.526880         0       0  
1        -0.417375   -1.329810         0       0  
2         3.130770    1.280580         0       0  
3         0.000000    0.000000         0       0  
4         2.080190   -0.608642         0       0  
...            ...         ...       ...     ...  
514106    0.644794   -1.211050         0       0  
514107   -2.496750    0.099627         0       0  
514108    0.006118   -3.149410         0       0  
514109    2.044300    1.632780         0       0  
514110    1.947170    3.083000         0       0  

[514111 rows x 14 columns]

ion      mass          mc      mc_low       mc_up  \
0               ${}^{1}H^{+}$    1.0100    0.951495    0.833554    1.266985   
1  ${}^{1}H_{2}{}^{16}O)^{+}$   18.0150   17.854743   17.798721   18.318838   
2     ${}^{12}C{}^{16}O)^{+}$   27.9950   27.756646   27.564403   28.418881   
3            ${}^{182}W^{3+}$   60.6500   60.662970   60.507878   60.928925   
4            ${}^{182}W^{2+}$   90.9750   90.968794   90.727016   91.346203   
5  $({}^{182}W{}^{16}O)^{2+}$   98.9725   98.870313   98.603767   99.210570   
6  $({}^{186}W{}^{18}O)^{2+}$  101.9750  106.771831  106.530053  107.062554   
7             ${}^{184}W^{+}$  183.9500  181.886266  181.669256  182.238908   
8         ${}^{184}W{}^{16}O$  199.9450  197.589284  197.198901  198.127681   
9     ${}^{16}O_{2}{}^{182}W$  213.9400  213.292302  212.951454  213.657327   

     color element complex   isotope  charge  
0  #b2aa2d     [H]     [1]       [1]       1  
1  #40344c  [H, O]  [2, 1]   [1, 16]       1  
2  #55577e  [C, O]  [1, 1]  [12, 16]       1  
3  #ab70d5     [W]     [1]     [182]       3  
4  #ab70d5     [W]     [1]     [182]       2  
5  #ea41ff  [W, O]     [1]     [182]       2  
6  #e2a63f  [W, O]     [1]     [186]       2  
7  #ab70d5     [W]     [1]     [184]       1  
8  #dbdfc8  [W, O]     [1]     [184]       1  
9  #45522f  [O, W]     [2]      [16]       1

<div style="margin: 0 auto; padding: 20px;">

# Temporal crop

Select the data by drawing a rectangle over the experiment history. Experiment history is a 2D histogram of the time of flight of the ions versus sequence of evaporation. The experiment history is plotted by clicking on the button below te cell.
</div>


In [6]:
helper_temporal_crop.call_plot_crop_experiment(variables)

Output()

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

# Spacial crop

Select the region of maximum concentration of Ions in the below plotted graph to utilize relevant data. To crop you can draw a circle over the filed desorption map. The field desorption map is a 2D histogram of the time of flight of the ions versus the position of the ions on the detector. The field desorption map is plotted by clicking on the button below the cell.
</div>

In [7]:
helper_special_crop.call_plot_crop_fdm(variables)

Output()

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

Calculate pulses since the last event pulse and ions per pulse. The percentage of loss in ROI selection process will be printed.
</div>

In [8]:
pulse_pi, ion_pp = data_loadcrop.calculate_ppi_and_ipp(variables.data)

# add two calculated array to the croped dataset
variables.data['pulse_pi'] = pulse_pi.astype(np.uintc)
variables.data['ion_pp'] = ion_pp.astype(np.uintc)

# exctract needed data from Pandas data frame as an numpy array
variables.dld_high_voltage = variables.data['high_voltage (V)'].to_numpy()
variables.dld_pulse = variables.data['pulse'].to_numpy()
variables.dld_t = variables.data['t (ns)'].to_numpy()
variables.dld_x_det = variables.data['x_det (cm)'].to_numpy()
variables.dld_y_det = variables.data['y_det (cm)'].to_numpy()

# save the cropped data
print('tof Crop Loss {:.2f} %'.format((100 - (len(variables.data) / len(variables.data)) * 100)))
#percentage of double event per pulse
print('percentage of double event per pulse', len(ion_pp[ion_pp != 1]) / float(len(ion_pp)))

tof Crop Loss 0.00 %
percentage of double event per pulse 0.018294776694819607


<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

In the next cell by changing the t<sub>0</sub> value you can correct the position of H<sub>1</sub> or any other known peak. this correction would be helpful for the position of the peaks in the m/c calibration process.
</div>

In [9]:
helper_t_0_tune.call_fine_tune_t_0(variables, flight_path_length, pulse_mode, t0)

Output()

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

Remove the data with m/c greater than max m/c and x, y, t = 0. Also add the needed colums for calibration. The data types of the final cropped dataset is displayed below.

</div>

In [10]:
# add the columns in the dataset for x, y, z, mc, mc calibrated, and t calibrated
helper_data_loader.add_columns(variables, max_mc)
# save data temporarily
data_tools.save_data(variables.data, variables, hdf=True, epos=False, pos=False, ato_6v=False, csv=False)
display(variables.data)
display(variables.data.dtypes)

The number of data over max_mc: 716225
The number of data with having t, x, and y equal to zero is: 0


x (nm)  y (nm)  z (nm)  mc_c (Da)    mc (Da)  high_voltage (V)  \
0            0.0     0.0     0.0        0.0  30.180069       5018.649902   
1            0.0     0.0     0.0        0.0  29.675168       5018.649902   
2            0.0     0.0     0.0        0.0  14.684399       5018.649902   
3            0.0     0.0     0.0        0.0  29.735116       5018.649902   
4            0.0     0.0     0.0        0.0  30.089277       5018.649902   
...          ...     ...     ...        ...        ...               ...   
10469695     0.0     0.0     0.0        0.0  23.875695       6367.229980   
10469696     0.0     0.0     0.0        0.0  30.521139       6367.229980   
10469697     0.0     0.0     0.0        0.0  30.250317       6367.229980   
10469698     0.0     0.0     0.0        0.0  29.494048       6367.229980   
10469699     0.0     0.0     0.0        0.0  30.102638       6367.229980   

                pulse  start_counter  t_c (ns)      t (ns)  x_det (cm)  \
0         1003.729980           8790       0.0  618.804199   -1.991837   
1         1003.729980           8867       0.0  604.690430   -0.107755   
2         1003.729980           9081       0.0  448.019409   -0.594286   
3         1003.729980           9239       0.0  615.299744   -1.756735   
4         1003.729980           9372       0.0  619.743774   -2.177959   
...               ...            ...       ...         ...         ...   
10469695  1273.446045           7752       0.0  496.135162   -0.277551   
10469696  1273.446045           7786       0.0  554.736755   -1.093878   
10469697  1273.446045           8098       0.0  549.524658   -1.358367   
10469698  1273.446045           8234       0.0  540.575012    0.767347   
10469699  1273.446045           8298       0.0  556.917603   -2.266122   

          y_det (cm)  pulse_pi  ion_pp  
0           0.395102        81       2  
1          -0.362449        77       1  
2          -2.608980       214       1  
3          -1.175510       158       1  
4           0.404898       133       1  
...              ...       ...     ...  
10469695   -1.942857       241       1  
10469696    1.433469        34       1  
10469697   -0.048980       312       1  
10469698   -0.195918       136       1  
10469699   -0.953469        12       1  

[10469700 rows x 14 columns]

x (nm)              float64
y (nm)              float64
z (nm)              float64
mc_c (Da)           float64
mc (Da)             float64
high_voltage (V)    float64
pulse               float64
start_counter        uint32
t_c (ns)            float64
t (ns)              float64
x_det (cm)          float64
y_det (cm)          float64
pulse_pi             uint32
ion_pp               uint32
dtype: object

-------------------------------------------------------
-------------------------------------------------------

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

## Time-of-Flight Calibration
</div>

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">
    
Below you can plot the ToF histogram of the dataset. You can select the peak range of the data you want to plot by drawing a rectangle over peak with holding left click. After that you should apply the voltage and bowl calibration. These three steps should be repeated until you see no improvement in the peak resolution. You can also save the calibration by clicking on the save button. The saved calibration will be used for the next steps.

</div>

In [11]:
# exctract needed data from Pandas data frame as an numpy array
data_tools.extract_data(variables.data, variables, flight_path_length.value, max_mc.value)
calibration_mode = widgets.Dropdown(
    options=[('time_of_flight', 'tof'), ('mass_to_charge', 'mc')],
    description='calibration mode:')
display(calibration_mode)

The maximum time of flight: 5010


Dropdown(description='calibration mode:', options=(('time_of_flight', 'tof'), ('mass_to_charge', 'mc')), value…

In [14]:
helper_calibration.call_voltage_bowl_calibration(variables, det_diam, calibration_mode)

Output()

In [75]:
variables.dld_t_calib_backup = np.copy(variables.dld_t_calib)
variables.mc_calib_backup = np.copy(variables.mc_calib)

In [76]:
helper_ion_list.call_ion_list(variables, selector='peak', calibration_mode=calibration_mode)

In [77]:
helper_mc_plot.call_mc_plot(variables, selector='None')

Output()

In [78]:
variables.data['mc_c (Da)'] = variables.mc_calib
variables.data['t_c (ns)'] = variables.dld_t_calib
# Remove negative mc
threshold = 0
mc_t = variables.data['mc_c (Da)'].to_numpy()
mc_t_mask = (mc_t <= threshold)
print('The number of ions with negative mc are:', len(mc_t_mask[mc_t_mask==True]))
variables.data.drop(np.where(mc_t_mask)[0], inplace=True)
variables.data.reset_index(inplace=True, drop=True)
# save data temporarily
data_tools.save_data(variables.data, variables, hdf=True, epos=False, pos=False, ato_6v=False, csv=False)

The number of ions with negative mc are: 0


-------------------------------------------------------
-------------------------------------------------------

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

## 3D Reconstruction
After bowl and voltage calibration we are ready to calculate the 3d reconstruction. In this workflow we calculate the reconstructed x,y,z and then plot the 3d, heatmap, projection plots and mass-to-charge histogram.

</div>

In [79]:
# exctract needed data from Pandas data frame as an numpy array
data_tools.extract_data(variables.data, variables, flight_path_length.value, max_mc.value)

display(variables.data)

The maximum time of flight: 11251


x (nm)  y (nm)  z (nm)  mc_c (Da)     mc (Da)  high_voltage (V)  \
0          0.0     0.0     0.0  92.114744   96.632159       7825.044434   
1          0.0     0.0     0.0  90.535085   95.165440       7825.044434   
2          0.0     0.0     0.0  90.998621   94.763123       7825.044434   
3          0.0     0.0     0.0   5.961612    6.181229       7825.044434   
4          0.0     0.0     0.0  91.022217   95.221722       7825.044434   
...        ...     ...     ...        ...         ...               ...   
514106     0.0     0.0     0.0  91.027713   95.519249       6566.107910   
514107     0.0     0.0     0.0   3.279549    3.385214       6566.107910   
514108     0.0     0.0     0.0  90.619730   95.513570       6566.107910   
514109     0.0     0.0     0.0   3.549455    3.636425       6566.107910   
514110     0.0     0.0     0.0  98.930123  102.882996       6566.107910   

               pulse  start_counter    t_c (ns)  t (ns)  x_det (cm)  \
0       1.201232e+12              0   96.667549  2022.0    2.461500   
1       1.201232e+12              0   94.964807  1990.0   -0.417375   
2       1.201232e+12              0   95.423833  2001.0    3.130770   
3       1.201232e+12              0    6.186905   525.0    0.000000   
4       1.201232e+12              0   95.497601  1995.0    2.080190   
...              ...            ...         ...     ...         ...   
514106  1.839976e+12              0   95.445040  2174.0    0.644794   
514107  1.839976e+12              0    3.376764   431.0   -2.496750   
514108  1.839976e+12              0   94.976538  2188.0    0.006118   
514109  1.839976e+12              0    3.656434   446.0    2.044300   
514110  1.839976e+12              0  103.610663  2276.0    1.947170   

        y_det (cm)  pulse_pi  ion_pp  
0        -2.526880         0       0  
1        -1.329810         0       0  
2         1.280580         0       0  
3         0.000000         0       0  
4        -0.608642         0       0  
...            ...       ...     ...  
514106   -1.211050         0       0  
514107    0.099627         0       0  
514108   -3.149410         0       0  
514109    1.632780         0       0  
514110    3.083000         0       0  

[514111 rows x 14 columns]

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

You have to select the main element in your sample from the from dropdown below.
</div>

In [80]:
element_selected = wd.density_field_selection()
display(element_selected)

Dropdown(description='Element', options=((1, 'H', 52.7, 0.0), (2, 'He', 28.7, 0.0), (3, 'Li', 46.3, 14.0), (4,…

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

In case that yopu face error about plotly library, like javascripts error. You have check your jupyter lab version is compatibale with the plotly extenstion. Sometimes running `jupyter lab build` command fix the proble.
</div>

In [84]:
helper_3d_reconstruction.call_x_y_z_calculation(variables, flight_path_length, element_selected)

Output()

In [85]:
variables.data['x (nm)'] = variables.x
variables.data['y (nm)'] = variables.y
variables.data['z (nm)'] = variables.z
# save data temporarily
data_tools.save_data(variables.data, variables, hdf=True, epos=False, pos=False, ato_6v=False, csv=False)

-------------------------------------------------------
-------------------------------------------------------

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

## Ion Selection and Rangging

This tutorial outlines a comprehensive workflow for ion selection and organization. Users can choose ions using peak and element finders, manually add ions, customize ion colors, and create histograms. Histograms can be generated for selected ranges and areas, and figures can be saved. Additionally, users have the option to save both figures and data in CSV and HDF5 formats.

</div>

In [86]:
# exctract needed data from Pandas data frame as an numpy array
data_tools.extract_data(variables.data, variables, flight_path_length.value, max_mc.value)

display(variables.data)

The maximum time of flight: 11251


x (nm)    y (nm)      z (nm)  mc_c (Da)     mc (Da)  \
0       2.638314 -2.708391    0.376799  92.114744   96.632159   
1      -0.452708 -1.442385    0.060484  90.535085   95.165440   
2       3.359438  1.374112    0.347794  90.998621   94.763123   
3       0.000000  0.000000    0.001620   5.961612    6.181229   
4       2.249210 -0.658095    0.145741  91.022217   95.221722   
...          ...       ...         ...        ...         ...   
514106  0.586899 -1.102312  217.152727  91.027713   95.519249   
514107 -2.261312  0.090232  217.264694   3.279549    3.385214   
514108  0.005518 -2.840600  217.358029  90.619730   95.513570   
514109  1.850265  1.477804  217.281094   3.549455    3.636425   
514110  1.749592  2.770171  217.443550  98.930123  102.882996   

        high_voltage (V)         pulse  start_counter    t_c (ns)  t (ns)  \
0            7825.044434  1.201232e+12              0   96.667549  2022.0   
1            7825.044434  1.201232e+12              0   94.964807  1990.0   
2            7825.044434  1.201232e+12              0   95.423833  2001.0   
3            7825.044434  1.201232e+12              0    6.186905   525.0   
4            7825.044434  1.201232e+12              0   95.497601  1995.0   
...                  ...           ...            ...         ...     ...   
514106       6566.107910  1.839976e+12              0   95.445040  2174.0   
514107       6566.107910  1.839976e+12              0    3.376764   431.0   
514108       6566.107910  1.839976e+12              0   94.976538  2188.0   
514109       6566.107910  1.839976e+12              0    3.656434   446.0   
514110       6566.107910  1.839976e+12              0  103.610663  2276.0   

        x_det (cm)  y_det (cm)  pulse_pi  ion_pp  
0         2.461500   -2.526880         0       0  
1        -0.417375   -1.329810         0       0  
2         3.130770    1.280580         0       0  
3         0.000000    0.000000         0       0  
4         2.080190   -0.608642         0       0  
...            ...         ...       ...     ...  
514106    0.644794   -1.211050         0       0  
514107   -2.496750    0.099627         0       0  
514108    0.006118   -3.149410         0       0  
514109    2.044300    1.632780         0       0  
514110    1.947170    3.083000         0       0  

[514111 rows x 14 columns]

In [87]:
helper_ion_selection.call_ion_selection(variables)

In [88]:
variables.range_data

ion      mass          mc      mc_low       mc_up  \
0               ${}^{1}H^{+}$    1.0100    0.951495    0.833554    1.266985   
1  ${}^{1}H_{2}{}^{16}O)^{+}$   18.0150   17.854743   17.798721   18.318838   
2     ${}^{12}C{}^{16}O)^{+}$   27.9950   27.756646   27.564403   28.418881   
3            ${}^{182}W^{3+}$   60.6500   60.662970   60.507878   60.928925   
4            ${}^{182}W^{2+}$   90.9750   90.968794   90.727016   91.346203   
5  $({}^{182}W{}^{16}O)^{2+}$   98.9725   98.870313   98.603767   99.210570   
6  $({}^{186}W{}^{18}O)^{2+}$  101.9750  106.771831  106.530053  107.062554   
7             ${}^{184}W^{+}$  183.9500  181.886266  181.669256  182.238908   
8         ${}^{184}W{}^{16}O$  199.9450  197.589284  197.198901  198.127681   
9     ${}^{16}O_{2}{}^{182}W$  213.9400  213.292302  212.951454  213.657327   

     color element complex   isotope  charge  
0  #b2aa2d     [H]     [1]       [1]       1  
1  #40344c  [H, O]  [2, 1]   [1, 16]       1  
2  #55577e  [C, O]  [1, 1]  [12, 16]       1  
3  #ab70d5     [W]     [1]     [182]       3  
4  #ab70d5     [W]     [1]     [182]       2  
5  #ea41ff  [W, O]     [1]     [182]       2  
6  #e2a63f  [W, O]     [1]     [186]       2  
7  #ab70d5     [W]     [1]     [184]       1  
8  #dbdfc8  [W, O]     [1]     [184]       1  
9  #45522f  [O, W]     [2]      [16]       1

In [89]:
variables.range_data.dtypes

ion         object
mass       float64
mc         float64
mc_low     float64
mc_up      float64
color       object
element     object
complex     object
isotope     object
charge      uint32
dtype: object

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

Save the range in the hdf5 and csv format.

</div>

In [90]:
# save the new data
name_save_file = variables.result_data_path + '/' + 'range_' + variables.dataset_name + '.h5'
data_tools.store_df_to_hdf(variables.range_data,  'df', name_save_file)
# save data in csv format
name_save_file = variables.result_data_path + '/' + 'range_' + variables.dataset_name + '.csv'
data_tools.store_df_to_csv(variables.range_data, name_save_file)

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

Save the cropped dataset. You can specify te output format from list below. The output formats are HDF5, EPOS, POS, ATO, and CSV. The output file will be saved in the same directory as the original dataset file in a new directory nammed load_crop.
</div>

In [91]:
interact_manual(data_tools.save_data, data=fixed(variables.data), variables=fixed(variables),
                hdf=widgets.Dropdown(options=[('True', True), ('False', False)]),
                epos=widgets.Dropdown(options=[('False', False), ('True', True)]),
                pos=widgets.Dropdown(options=[('False', False), ('True', True)]),
                ato_6v=widgets.Dropdown(options=[('False', False), ('True', True)]),
                csv=widgets.Dropdown(options=[('False', False), ('True', True)]));

interactive(children=(Dropdown(description='hdf', options=(('True', True), ('False', False)), value=True), Dro…

-------------------------------------------------------
-------------------------------------------------------

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">
    
# Visualization
    
</div>

In [26]:
helper_visualization.call_visualization(variables)

Output()